In [1]:
import os
import fnmatch
import shutil
import random
import json
import csv
import pandas as pd
# Set the Pandas options to display all rows and columns
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

pd.set_option('display.width', None)  # or any number you prefer
# pd.set_option('display.max_columns', 20)  # or any number you prefer

pd.set_option('display.max_colwidth', None)


In [2]:
! wget -O  mobilenet.json -q https://gist.githubusercontent.com/mbostock/535395e279f5b83d732ea6e36932a9eb/raw/62863328f4841fce9452bc7e2f7b5e02b40f8f3d/mobilenet.json
! wget -O imagenet_class_index.json -q https://s3.amazonaws.com/deep-learning-models/image-models/imagenet_class_index.json
! wget -O imagenet-simple-labels.json -q https://raw.githubusercontent.com/anishathalye/imagenet-simple-labels/master/imagenet-simple-labels.json    

In [3]:
def generate_parent_mapping(data, parent=None, result=None):
    if result is None:
        result = {}
    if 'children' in data:
        for child in data['children']:
            result[child['id']] = data['id']
            generate_parent_mapping(child, data['id'], result)
    return result

def generate_id_to_name_mapping(data, result=None):
    if result is None:
        result = {}
    result[data['id']] = data['name']
    if 'children' in data:
        for child in data['children']:
            generate_id_to_name_mapping(child, result)
    return result


with open('mobilenet.json', 'r') as f:
    json_data = json.load(f)
Nname2parentNname = generate_parent_mapping(json_data)
Nname2name = generate_id_to_name_mapping(json_data)

with open('imagenet_class_index.json', 'r') as f:
    data = json.load(f)
    idx2Nname = {}
    for k, v in data.items():
        idx2Nname[int(k)] = v[0]
    Nname2idx = {v: k for k, v in idx2Nname.items()}
    idx2parentName = {k: Nname2name[Nname2parentNname[v]] for k, v in idx2Nname.items()}

with open('imagenet-simple-labels.json', 'r') as f:
    data = json.load(f)
    idx2classname = {i: data[i] for i in range(len(data))}


In [4]:
idx2classname

{0: 'tench',
 1: 'goldfish',
 2: 'great white shark',
 3: 'tiger shark',
 4: 'hammerhead shark',
 5: 'electric ray',
 6: 'stingray',
 7: 'cock',
 8: 'hen',
 9: 'ostrich',
 10: 'brambling',
 11: 'goldfinch',
 12: 'house finch',
 13: 'junco',
 14: 'indigo bunting',
 15: 'American robin',
 16: 'bulbul',
 17: 'jay',
 18: 'magpie',
 19: 'chickadee',
 20: 'American dipper',
 21: 'kite',
 22: 'bald eagle',
 23: 'vulture',
 24: 'great grey owl',
 25: 'fire salamander',
 26: 'smooth newt',
 27: 'newt',
 28: 'spotted salamander',
 29: 'axolotl',
 30: 'American bullfrog',
 31: 'tree frog',
 32: 'tailed frog',
 33: 'loggerhead sea turtle',
 34: 'leatherback sea turtle',
 35: 'mud turtle',
 36: 'terrapin',
 37: 'box turtle',
 38: 'banded gecko',
 39: 'green iguana',
 40: 'Carolina anole',
 41: 'desert grassland whiptail lizard',
 42: 'agama',
 43: 'frilled-necked lizard',
 44: 'alligator lizard',
 45: 'Gila monster',
 46: 'European green lizard',
 47: 'chameleon',
 48: 'Komodo dragon',
 49: 'Nile c

In [5]:
idx2parentName_simple = {}
name2parentname = {}
lines = []
with open('label2parentlael.txt', 'r') as f:
    i = 0
    for line in f:
        idx = int(line.split(',')[0])
        class_name = line.split(',')[1].split(':')[0].strip()
        parent_name = line.split(':')[1].strip()
#         print(line.strip(), idx, parent_name)
        idx2parentName_simple[idx] = parent_name
        name2parentname[class_name] = parent_name
name2parentname['automated teller machine'] = 'machine'

In [6]:
imagenetr_idx2Nname = {}
imagenetr_idx2name = {}
with open('imagenetr_mapping.csv', 'r') as f:
    for line in f:
        line = line.strip()
        Nname, idx = line.split(', ')[0], int(line.split(', ')[1])
        imagenetr_idx2Nname[idx] = Nname
        class_name = idx2classname[Nname2idx[Nname]]
        imagenetr_idx2name[idx] = class_name
        print(idx, Nname, class_name, name2parentname[class_name])

0 n03272010 electric guitar guitar
1 n02123045 tabby cat domestic cat
2 n09835506 baseball player athlete
3 n02363005 beaver rodent
4 n07720875 bell pepper sweet pepper
5 n07768694 pomegranate edible fruit
6 n01616318 vulture bird
7 n02119022 red fox fox
8 n03649909 lawn mower garden tool
9 n01534433 junco bird
10 n07734744 mushroom vegetable
11 n02814860 lighthouse tower
12 n01983481 American lobster lobster
13 n02749479 assault rifle automatic rifle
14 n04536866 violin musical instrument
15 n04310018 steam locomotive train
16 n01443537 goldfish fish
17 n03467068 guillotine instrument
18 n02097298 Scottish Terrier hunting dog
19 n02951358 canoe small boat
20 n01531178 goldfinch bird
21 n02233338 cockroach insect
22 n02110958 pug dog
23 n02112137 Chow Chow dog
24 n02672831 accordion musical instrument
25 n04552348 military aircraft military vehicle
26 n07695742 pretzel pretzel
27 n03630383 lab coat coat
28 n01986214 hermit crab crab
29 n10565667 scuba diver diver
30 n02110185 Siberian 

## Generate csv file for human study

In [50]:

def find_png_files(directory):
    for root, dirs, files in os.walk(directory):
        for file in files:
            if fnmatch.fnmatch(file, '*.png'):
                yield os.path.join(root, file)
    

In [51]:
attacks = "elastic  gabor  glitch  jpeg  kaleidescope  pixel  snow  wood".split()
savedir = './results/humanstudy/all_images'


In [52]:
os.makedirs(savedir, exist_ok=True)

for attack in attacks:
    files = find_png_files(f'./results/humanstudy/{attack}')
    for f in files:
        shutil.copy(f, os.path.join(savedir, f'{attack}_medium_{os.path.basename(f)}'))

### Upload the images to AWS

In `experiments/results/humanstudy/all_images` run `aws s3 cp .  s3://corruptions-human-study/all_images/ --recursive --exclude "*" --include "*.png" --acl public-read`

In [57]:
random.seed(123)
data = []
for f in find_png_files(savedir):
    tokens = os.path.splitext(os.path.basename(f))[0].split('_')
    gt = int(tokens[-2])
    predicted = int(tokens[-1])
    candidates = list(set(range(200)) - set([gt, predicted]))
    sampled_numbers = random.sample(candidates, 3)
    labels = [gt, predicted] + sampled_numbers
    random.shuffle(labels)
    assert len(labels) == len(set(labels))
    url = '' + os.path.basename(f)
    label_names = []
    for label_idx in labels:
        class_name = imagenetr_idx2name[label_idx]
        if class_name == 'ear':
            class_name = 'capitulum'
        parent_name = name2parentname[class_name]
        assert len(parent_name) > 0
        label_names.append(f'{class_name} (type of {parent_name})')
    data.append([url] + label_names)


In [58]:
with open('humanstudy_imagenetr_fixed.csv', 'w', newline='') as f:
    writer = csv.writer(f)
    writer.writerow(['url', 'label1', 'label2', 'label3', 'label4', 'label5'])
    writer.writerows(data)

## Analyze Human study result

In [7]:
pred_df = pd.read_csv('Adversarial_Images_Classification_results.csv', index_col=0)

In [8]:
pred_df

task_id  \
worker_id                                            
H2PRAMNFTQ44  860aa826-1c25-4028-8bf1-51053727b53a   
ZPXXFV77FFQK  8dba7db4-61e5-420b-a388-4570d2469f34   
HWA9FD7CGF2T  b01891c0-072b-4de1-b764-014ffc951a2b   
6XKP4FFDQ2T3  11e005f3-847d-4a8e-810c-79a596716549   
YECRDY9WT76X  02b4a64e-3211-4287-9777-77c50fe4856a   
ZPXXFV77FFQK  37eb8b4b-9b5b-49fa-a172-8a05ed987bc7   
HWA9FD7CGF2T  f88330ae-aabc-4da0-b9b4-2af977579d22   
EDQCT4ZZMXJ4  2d624b1e-b4ee-4d9f-9caf-797942e949fe   
H2PRAMNFTQ44  26f3db95-1818-4925-b318-3bcc6ac5d187   
6XKP4FFDQ2T3  ed4f5cc6-9ad1-417a-a87f-7be7dfb03597   
HWA9FD7CGF2T  eafe1b3f-c152-4d88-91fd-9ffa48d0177e   
47MV9WYPKKKQ  a1ee441c-7876-4c5b-9c0a-4b3e46c2fa66   
2P4YM2ZXEHWN  6e7c4b44-a972-4048-a973-a5e714477f57   
6XKP4FFDQ2T3  4375b88e-a07f-44dc-8074-470678685f52   
ZPXXFV77FFQK  bdfef1aa-c89a-48bd-9040-7832eccb76cc   
HWA9FD7CGF2T  8aa38813-8247-4fa5-8a3a-4bb7b696f241   
HWA9FD7CGF2T  10d4bb0b-1d15-4fa1-a96f-ec8067841bd5   
H2PRAMNFTQ44  d83b8046-2d58-44bd-a7cd-22833b1e5787   
47MV9WYPKKKQ  e3d304d9-44a8-4966-9e6c-c53a8b9ce46b   
ZPXXFV77FFQK  a6289b69-a65a-495e-b0cc-ab6b6210dcaa   
H2PRAMNFTQ44  769c6d44-c1f2-4cb2-bce2-f485a9388efc   
47MV9WYPKKKQ  181736e7-e776-4c10-ae7e-76a5b1b0ccba   
EV3TZCMTRCKM  5987f4c2-606b-4ee5-be14-77ba46c1eb6e   
FEZH36M74KJY  12437b8b-7b26-4e8e-b959-67325677e3be   
FH2X3PCXWHKT  c6454fe7-52ba-4ac0-aff6-17829d97d4e2   
HWA9FD7CGF2T  9d8ad459-56da-4cf3-8b37-5f63b173497a   
4JRJDQE2PGTD  7cca1372-a77e-47ae-a516-d6897f2b8250   
WM7NAQGNQGYK  5f220dea-0b78-452e-8d61-376683e66984   
Q9JDECXTH26V  7ce68ee6-d3c3-4faf-a30d-57a3d10f8d39   
AJ43PYZXFG6Z  6da63120-2962-4edd-a0f6-41a7b4291068   
PH2T2A97ARHX  154c3828-6c8c-4fc5-b31b-9f4f7b56975d   
ZPXXFV77FFQK  70f0f668-b3b0-4857-b4d9-eba23b3583f3   
FXTWTGPVGMCD  fe4459ae-9b00-48d5-8f6c-258bbd45395b   
6RGDXJA23CDH  7957bc90-4138-4d7d-8ab1-6a56fab8b760   
9R76YRV26ZAY  f77e1ae3-b1bd-48ee-a475-fca4c048d7e5   
EX3YW37MDNYX  c14bb987-fbdd-4f85-9c8a-03ec688e6964   
RNYP7FRC9CAP  89c2f039-ed7a-4059-aeb2-0c1d0e4a58cc   
RNYP7FRC9CAP  7c22d147-301f-4832-9c1a-62cd672a6a46   
4ET2VQ3W9VWE  16b8832b-ed0d-4bce-9aff-5f76dbeb9685   
VAKEQ9K2EGHG  e558560c-729e-4b7e-9dbd-209bf9aed820   
763XG6NFETWP  1a219f0e-fcbc-4122-abf0-876cce362201   
JVVN3RMXAFVH  4529ec3f-0b0d-4ae6-9a4f-348b92b5fe09   
ACZJEM4RDCNF  4d0c56de-a616-40e1-ba0c-a412320d13a1   
R2KFYN2MA49J  cc32cb9c-2855-4a2b-a4e5-ac9f13c5ee19   
264V9NQFWYQ7  404ce132-3353-4410-909f-996cbd183755   
PM2H3FRF7APT  82346868-9af9-4e92-96ce-ce205196b5d2   
XH46NJKRNVKN  bf83f873-d145-4b8a-85c6-3dd01a403370   
REK2VT9G42V2  db16496b-4996-45b3-b90d-10b764bdae57   
CH643KRCHKDF  5a92ca5a-c7af-4647-9d99-1534e4adae70   
927WV6DCYYQV  f9787cfd-6e7c-4ca3-806f-9a87ddcc07b2   
ZVFYREF73ZFJ  209990be-4bca-4384-9faf-9b7a16d732e0   
HZVYME49CFPF  eecc9a4f-3548-46f9-8f07-11fa886acb16   
XK4N4W94XGNP  c2e60bd0-d446-4d82-aa4f-7efef882c66b   
EGZJWKZXW9RW  f7fe24cf-ac9d-4593-a1a6-7612b8361963   
CZTPPMCT397J  c63a27a5-6beb-450c-ac97-37be2123d92b   
Q9GEWENQTWDC  7711b1e1-26d2-47d1-a497-3a0f6bd47aff   
D636Y3ZEYYX4  7967b291-f905-46bd-b2d6-122ef41d0369   
YE3GDX3NTDQW  8c26c572-f692-4550-9ffb-c5be31eda487   
MQCV6WZGCDX4  9337762f-2e07-4971-b2e2-7cf8166deede   
CXVGDDCQD46W  85a982ad-0c6d-420c-9f37-3dfa6de4000e   
HVDJPXDM6X3Z  2a9e3366-a588-44dd-8532-f5e96df7d2d0   
K6CWNH7NCWQC  c6b2051b-c0ee-484d-8f83-b16bdbded6ba   
4GR3RNVP3RYA  525396a0-ef7a-46e1-8b38-27f95c2c5f62   
K69FNNE272EG  489a1d8b-3536-4515-9979-f1e063d52ed3   
Q3MQJ47XVP43  5e620a0c-422b-4eea-9c35-89b41135125a   
264V9NQFWYQ7  211ea2a3-6f0e-47ba-9fa1-f580d679f02b   
4ZN4YMVG9QDC  453d45e5-8b48-4cfb-a64c-abcbba7e205b   
JEFYJD6E7KEN  4e7e1ad3-a26a-485f-a2d9-b5196a4edb91   
MMYAV7CJYGKR  41a84108-779f-443e-8a4c-886d286f8eba   
2AJKHV2QFNDG  b22cbae2-b770-4b46-a998-032ea3b2ba0f   
E6RK6AKCY9DD  1dee7a95-f5b3-43db-8652-00d694682371   
JY7QDFRRMNE3  eb7ecef6-bd01-4513-99a7-c8b61141da46   
FGR2YZAPY3E9  2e97f4f5-568c-44d1-9396-0a1c352c0

### Average accuracy

In [9]:
answers = {'{{label1}}': 'label1', 
           '{{label2}}': 'label2', 
           '{{label3}}': 'label3', 
           '{{label4}}': 'label4', 
           '{{label5}}': 'label5'}
N, N_corrupted, N_uncorrupted, correct = 0, 0, 0, 0
for index, row in pred_df.iterrows():
    if row.isna()['url']:
        continue
    url = row['url']
    pred_id = row[pred_df.columns[-1]]
    tokens = os.path.splitext(os.path.basename(url))[0].split('_')
    gt = imagenetr_idx2name[int(tokens[-2])]
    if pred_id in answers.keys():
        pred = row[answers[pred_id]]
        N_uncorrupted += 1
        if gt in pred:
            correct += 1        
    else:
        N_corrupted += 1
    N += 1
print('accuracy', correct/N_uncorrupted)
print('corrupted', N_corrupted/N)

accuracy 0.9497645211930926
corrupted 0.0445


### Majority voting accuracy

In [24]:
answers = {'{{label1}}': 'label1', 
           '{{label2}}': 'label2', 
           '{{label3}}': 'label3', 
           '{{label4}}': 'label4', 
           '{{label5}}': 'label5'}
attacks = "elastic  gabor  glitch  jpeg  kaleidescope  pixel  snow  wood".split()
for attack in attacks:
    rows = []
    N, N_corrupted, N_uncorrupted, correct = 0, 0, 0, 0
    for index, row in pred_df.iterrows():
        if row.isna()['url']:
            continue
        url = row['url']
        if attack not in url:
            continue
        pred_id = row[pred_df.columns[-1]]
        tokens = os.path.splitext(os.path.basename(url))[0].split('_')
        gt = imagenetr_idx2name[int(tokens[-2])]
        if pred_id in answers.keys():
            pred = row[answers[pred_id]]
            N_uncorrupted += 1
            if gt in pred:
                correct += 1
                rows.append({'url': url, 'correct': 1.0})
            else:
                rows.append({'url': url, 'correct': 0})
        else:
            N_corrupted += 1
            rows.append({'url': url, 'correct': 0})
        N += 1
    df = pd.DataFrame(rows)
    acc = df['correct'].mean()
    grouped = df.groupby('url').mean()
    majority_votting_acc = (grouped['correct'] > 2/3).mean()
    print(f'{attack}, average accuracy {round(correct/N_uncorrupted,4)}, corrupted {N_corrupted/N:.4f}')    
#     print(f'{attack}, average accuracy {correct/N_uncorrupted:.4f}, corrupted {N_corrupted/N:.3f}, {N_corrupted, N}')
#     print(f'{attack}, average accuracy {acc:.3f}, majority voting accuracy {majority_votting_acc:.3f}')

elastic, average accuracy 0.9388, corrupted 0.0200
gabor, average accuracy 0.9729, corrupted 0.0400
glitch, average accuracy 0.9548, corrupted 0.1600
jpeg, average accuracy 0.9396, corrupted 0.0060
kaleidescope, average accuracy 0.9915, corrupted 0.0620
pixel, average accuracy 0.943, corrupted 0.0180
snow, average accuracy 0.9298, corrupted 0.0320
wood, average accuracy 0.9308, corrupted 0.0180
